In [3]:
import pandas as pd
import altair as alt
import numpy as np

alt.renderers.enable('default')

RendererRegistry.enable('default')

In [4]:
df = pd.read_csv('data/billionaires.csv', parse_dates=['birthDate'])
# df['education'] = df['education'].astype('Int64')

In [5]:
# Scale GDP to millions (matching finalWorth)
df['gdp_country'] = df['gdp_country']/1000000

In [4]:
# df = df.replace('', np.nan, regex=True)

# Task 1

In [6]:
cols_to_keep = list(set(df.columns).difference(['industry_sector', 'education']))

# Change the the dataframe to allow selection of variables
df_wide = pd.melt(df, cols_to_keep)

select_box = alt.binding_select(name="Color by: ", options=list(df_wide['variable'].unique()))
selection = alt.selection_point(value='education', fields=['variable'], bind=select_box)

viz1 = alt.Chart(df_wide.dropna()).mark_line(
    point=True
).encode(
    x=alt.X('decade:N', title="Decade the Billionaire was Born in"),
    y=alt.Y('median(finalWorth):Q', title="Median Final Worth (in Millions USD)"),
    color=alt.Color('value', legend=alt.Legend(
        orient='none',
        legendX=300, legendY=10,
        direction='vertical',
        titleAnchor='start', title="Color Legend")),
    tooltip=['decade', 'median(finalWorth)', 'value']
).add_selection(
    selection
).transform_filter(
    selection
).properties(
    width=500,
    height=300,
    title="Median Final Worth of Billionares (in millions USD) based on the Decade They Were Born in"
)

# credit to https://github.com/altair-viz/altair/issues/965
viz1

/Users/kevin/anaconda3/envs/320/lib/python3.11/site-packages/altair/utils/deprecation.py:65: AltairDeprecationWarning: 'add_selection' is deprecated. Use 'add_params' instead.
  warnings.warn(message, AltairDeprecationWarning, stacklevel=1)


alt.Chart(...)

In [6]:
# df['industries'].value_counts(dropna=False)

# Task 2

In [7]:
gdf = df.groupby(['country', 'continent', 'gdp_country']).agg({'personName':'count', 'finalWorth': 'sum'}).rename(
    columns = {'personName':'num_billionaires', 'finalWorth':'totalWorth'}
).reset_index()

In [8]:
gdf.head()

country continent  gdp_country  num_billionaires  totalWorth
0  Argentina  Americas     449663.0                 4       11000
1  Australia   Oceania    1392680.0                43      173500
2    Austria    Europe     446315.0                11       75400
3    Belgium    Europe     529607.0                 3       41200
4     Brazil  Americas    1839760.0                44      104800

In [9]:
bind = alt.selection_interval(bind='scales')

# input_checkbox = alt.binding_checkbox()
# scale_select = alt.selection_point(bind=input_checkbox)
# type_checkbox_condition = alt.condition(scale_select,
#                                         alt.Scale(type='log'),
#                                         alt.Scale(type='linear')
#                                        )

alt.Chart(gdf).mark_circle().encode(
    y=alt.Y("gdp_country:Q",
            scale=alt.Scale(type='log'),
            # scale=type_checkbox_condition,
            title="Country GDP (per million USD)"),
    x=alt.X("totalWorth",
            scale=alt.Scale(type='log'),
            # scale=type_checkbox_condition,
            title="Total Net Worth of Country's Billionaires"),
    size=alt.Size("num_billionaires", scale=alt.Scale(range=[25, 800])),
    color="continent",
    tooltip=["country", 'num_billionaires', 'gdp_country:Q'],
).properties(
    height=500,
    width=500
).add_params(
    bind
    # type_checkbox_condition
)

alt.Chart(...)

# Choropleth (Task 2)

In [10]:
country_ids = pd.read_csv('https://raw.githubusercontent.com/joelostblom/teaching-datasets/main/country-ids-and-continents.csv')
relevant_country_names = country_ids["Country"]

mapping = {'South America': 'Americas',
           'North America': 'Americas'}

country_ids.Continent = country_ids.Continent.replace(mapping)
country_ids

ID         Country   Continent
0      4     Afghanistan        Asia
1      8         Albania      Europe
2     12         Algeria      Africa
3     24          Angola      Africa
4     10      Antarctica  Antarctica
..   ...             ...         ...
169  704         Vietnam        Asia
170  732  Western Sahara      Africa
171  887           Yemen        Asia
172  894          Zambia      Africa
173  716        Zimbabwe      Africa

[174 rows x 3 columns]

In [11]:
from vega_datasets import data
import vegafusion as vf
vf.enable_widget()
alt.renderers.enable('default')

world = data.world_110m.url
world_map = alt.topo_feature(world, "countries")

# # Create a chart using the data above and geoshape mark
# country_map = alt.Chart(world_map).mark_geoshape()
# # Show the chart
# country_map

In [12]:
wdf_og = pd.merge(df, country_ids,  how='right', left_on=['country', 'continent'], right_on = ['Country', 'Continent'])
wdf_og = wdf_og.dropna(subset=['ID'])
wdf_og

finalWorth         personName   age  country       industries status  \
0            NaN                NaN   NaN      NaN              NaN    NaN   
1            NaN                NaN   NaN      NaN              NaN    NaN   
2            NaN                NaN   NaN      NaN              NaN    NaN   
3            NaN                NaN   NaN      NaN              NaN    NaN   
4            NaN                NaN   NaN      NaN              NaN    NaN   
...          ...                ...   ...      ...              ...    ...   
2597      1300.0  Nguyen Dang Quang  59.0  Vietnam  Food & Beverage      D   
2598         NaN                NaN   NaN      NaN              NaN    NaN   
2599         NaN                NaN   NaN      NaN              NaN    NaN   
2600         NaN                NaN   NaN      NaN              NaN    NaN   
2601         NaN                NaN   NaN      NaN              NaN    NaN   

     gender  birthDate  gdp_country  life_expectancy_country  \
0       NaN        NaT          NaN                      NaN   
1       NaN        NaT          NaN                      NaN   
2       NaN        NaT          NaN                      NaN   
3       NaN        NaT          NaN                      NaN   
4       NaN        NaT          NaN                      NaN   
...     ...        ...          ...                      ...   
2597      M 1963-08-23     261921.0                     75.3   
2598    NaN        NaT          NaN                      NaN   
2599    NaN        NaT          NaN                      NaN   
2600    NaN        NaT          NaN                      NaN   
2601    NaN        NaT          NaN                      NaN   

      total_tax_rate_country  economic_class  education continent  \
0                        NaN             NaN        NaN       NaN   
1                        NaN             NaN        NaN       NaN   
2                        NaN             NaN        NaN       NaN   
3                        NaN             NaN        NaN       NaN   
4                        NaN             NaN        NaN       NaN   
...                      ...             ...        ...       ...   
2597                    37.6             3.0        NaN      Asia   
2598                     NaN             NaN        NaN       NaN   
2599                     NaN             NaN        NaN       NaN   
2600                     NaN             NaN        NaN       NaN   
2601                     NaN             NaN        NaN       NaN   

                       industry_sector    year  decade   ID         Country  \
0                                  NaN     NaN     NaN    4     Afghanistan   
1                                  NaN     NaN     NaN    8         Albania   
2                                  NaN     NaN     NaN   12         Algeria   
3                                  NaN     NaN     NaN   24          Angola   
4                                  NaN     NaN     NaN   10      Antarctica   
...                                ...     ...     ...  ...             ...   
2597  Consumer Discretionary & Staples  1963.0  1960.0  704         Vietnam   
2598                               NaN     NaN     NaN  732  Western Sahara   
2599                               NaN     NaN     NaN  887           Yemen   
2600                               NaN     NaN     NaN  894          Zambia   
2601                               NaN     NaN     NaN  716        Zimbabwe   

       Continent  
0           Asia  
1         Europe  
2         Africa  
3         Africa  
4     Antarctica  
...          ...  
2597        Asia  
2598      Africa  
2599        Asia  
2600      Africa  
2601      Africa  

[2602 rows x 20 columns]

In [13]:
group_gender = wdf_og.fillna(0).groupby(['ID', 'Country', 'Continent'])['gender'].value_counts().unstack(fill_value=0).reset_index()
group_inds = wdf_og.fillna(0).groupby(['ID', 'Country', 'Continent'])['industry_sector'].value_counts().unstack(fill_value=0).reset_index()

wdf = pd.merge(group_gender, group_inds,  how='left', left_on=['ID', 'Country','Continent'], right_on = ['ID', 'Country', 'Continent'])
wdf.ID = wdf.ID.apply(lambda x: int(x))
wdf = wdf.drop(['0_x', '0_y'], axis=1)
wdf

ID      Country   Continent  F  M  Consumer Discretionary & Staples  \
0      4  Afghanistan        Asia  0  0                                 0   
1      8      Albania      Europe  0  0                                 0   
2     10   Antarctica  Antarctica  0  0                                 0   
3     12      Algeria      Africa  0  0                                 0   
4     24       Angola      Africa  0  0                                 0   
..   ...          ...         ... .. ..                               ...   
169  858      Uruguay    Americas  0  0                                 0   
170  860   Uzbekistan        Asia  0  0                                 0   
171  862    Venezuela    Americas  0  0                                 0   
172  887        Yemen        Asia  0  0                                 0   
173  894       Zambia      Africa  0  0                                 0   

     Diversified  Energy & Industrials & Materials  Financials  Service  \
0              0                                 0           0        0   
1              0                                 0           0        0   
2              0                                 0           0        0   
3              0                                 0           0        0   
4              0                                 0           0        0   
..           ...                               ...         ...      ...   
169            0                                 0           0        0   
170            0                                 0           0        0   
171            0                                 0           0        0   
172            0                                 0           0        0   
173            0                                 0           0        0   

     Technology  
0             0  
1             0  
2             0  
3             0  
4             0  
..          ...  
169           0  
170           0  
171           0  
172           0  
173           0  

[174 rows x 11 columns]

In [14]:
wdf.Continent.unique()

array(['Asia', 'Europe', 'Antarctica', 'Africa', 'Americas', 'Oceania'],
      dtype=object)

In [15]:
fields=wdf.columns.to_list()[1:]
# fields=['Country', 'Continent']
fields

['Country',
 'Continent',
 'F',
 'M',
 'Consumer Discretionary & Staples',
 'Diversified',
 'Energy & Industrials & Materials',
 'Financials',
 'Service',
 'Technology']

In [16]:
color_range =  ['#7fc97f','#beaed4', '#fdc086', '#795227','#386cb0', '#f0027f'] 

# sel_hover = alt.selection_point(on='mouseover', empty='none')
click = alt.selection_multi(encodings=['color'])

choropleth = alt.Chart(world_map).mark_geoshape(
    stroke=None
).transform_lookup(
    lookup='id', from_=alt.LookupData(data=wdf, key='ID', fields=fields)
).encode(
    # alt.Color('Continent:O', scale=alt.Scale(range=color_range)),
    color = alt.condition(click, alt.Color('Continent:O', scale=alt.Scale(range=color_range)), alt.value('lightgray')),
    tooltip = alt.Tooltip(['Country:O', 'Continent:O', 'F:Q', 'M:Q'])
).project(
    type="equalEarth"
).properties(
    width=600,
    height=300
).transform_filter(
    'isValid(datum.Continent)'
).add_params(
    click
)

choropleth

/Users/kevin/anaconda3/envs/320/lib/python3.11/site-packages/altair/utils/deprecation.py:65: AltairDeprecationWarning: 'selection_multi' is deprecated.  Use 'selection_point'
  warnings.warn(message, AltairDeprecationWarning, stacklevel=1)


alt.Chart(...)

In [17]:
gender_range = ['lightpink', 'lightblue']

# cdf = wdf_og.loc[wdf_og.Continent == 'Asia']

barplot = alt.Chart(wdf_og).mark_bar().encode(
    y=alt.Y('industry_sector', title="Industry Sector"),
    x=alt.X('count()', title="Count of Billionaires"),
    color=alt.Color('gender', scale=alt.Scale(domain = ['F', 'M'], range=gender_range), legend=alt.Legend(title="Gender")),
).transform_filter(
    'isValid(datum.gender)'
).properties(
    width=150,
    height=250
)
barplot

alt.Chart(...)

In [18]:
alt.hconcat(
    choropleth,
    barplot.transform_filter(click),
    center=True,
    title="Billionaire Gender Ratio By Continent",
).resolve_scale(
    color='independent'
).configure_legend(
    orient='bottom',
    direction='horizontal',
)

alt.HConcatChart(...)

# Task 3

In [19]:
req = ['finalWorth', 'country', 'gdp_country', 'life_expectancy_country']
df[req].info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 2657 entries, 0 to 2656
Data columns (total 4 columns):
 #   Column                   Non-Null Count  Dtype  
---  ------                   --------------  -----  
 0   finalWorth               2657 non-null   int64  
 1   country                  2657 non-null   object 
 2   gdp_country              2545 non-null   float64
 3   life_expectancy_country  2545 non-null   float64
dtypes: float64(2), int64(1), object(1)
memory usage: 83.2+ KB


In [20]:
#countries with null values in gdp_country
df[pd.isnull(df['gdp_country'])].country.unique()

array(['Hong Kong', 'Taiwan'], dtype=object)

In [21]:
#countries with null values in life_expectancy_country
df[pd.isnull(df['life_expectancy_country'])].country.unique()

array(['Hong Kong', 'Taiwan'], dtype=object)

In [22]:
#filling in the null values with the appropriate values (information obtained from Google) and manipulating dataset to fulfill needs
df['e_class'] = ''
df.loc[df['country'] == 'Hong Kong', 'gdp_country'] = 91400000000
df.loc[df['country'] == 'Hong Kong', 'life_expectancy_country'] = 85.3
df.loc[df['country'] == 'Taiwan', 'gdp_country'] = 185233000000
df.loc[df['country'] == 'Taiwan', 'life_expectancy_country'] = 81.0
df.loc[df['economic_class'] == 1, 'e_class'] = 'Developed'
df.loc[df['economic_class'] == 2, 'e_class'] = 'Emerging'
df.loc[df['economic_class'] == 3, 'e_class'] = 'Developing'


df['gdp_country'] = df['gdp_country'] / 10000000000

In [23]:
df['medianFinalWorth'] = df.groupby(['country'])['finalWorth'].transform('median')
req = ['medianFinalWorth', 'country', 'gdp_country', 'life_expectancy_country', 'economic_class', 'e_class']
task3df = df[req].drop_duplicates().reset_index().drop('index', axis=1)
task3df.head()

medianFinalWorth        country  gdp_country  life_expectancy_country  \
0            4200.0         France     0.000272                     82.5   
1            2900.0  United States     0.002143                     78.5   
2            4000.0         Mexico     0.000126                     75.0   
3            2100.0          India     0.000261                     69.4   
4            2100.0          Spain     0.000139                     83.3   

   economic_class    e_class  
0               1  Developed  
1               1  Developed  
2               2   Emerging  
3               2   Emerging  
4               1  Developed

In [24]:
splot_brush = alt.selection_interval(encodings=['x', 'y'], empty=False)
gdp_splot = alt.Chart(task3df).mark_point().encode(
    alt.X('gdp_country', title='Country GDP (billion USD)').scale(type='log'),
    alt.Y('medianFinalWorth', title='Median Final Net Worth (million USD)'),
     color = alt.condition(splot_brush, 'e_class:N', alt.value('lightgray'), title='Economic Class'),
    tooltip=[
             alt.Tooltip('country', title='Country'),
             alt.Tooltip('gdp_country', title='Country GDP (billion USD)'),
             alt.Tooltip('medianFinalWorth', title='Median Final Net worth (million USD)'), 
             ]
).add_params(splot_brush)

life_splot = alt.Chart(task3df).mark_point().encode(
    alt.X('life_expectancy_country', title='Country Life Expectancy (Years)').scale(zero=False),
    alt.Y('medianFinalWorth', title='Median Final Net Worth (million USD)'),
    alt.Color('e_class:N'),
    tooltip=[
             alt.Tooltip('country', title='Country'),
             alt.Tooltip('life_expectancy_country', title='Country Life Expectancy'),
             alt.Tooltip('medianFinalWorth', title='Median Final Net worth (million USD)'), 
             ]
)

gdp_splot | life_splot.encode(
    color = alt.condition(splot_brush, 'e_class:N', alt.value('lightgray'))
).add_params(splot_brush)

alt.HConcatChart(...)

### Task 4

In [25]:
df_top20_sector = df
df_top20_sector = df_top20_sector[df_top20_sector.groupby('industry_sector')['finalWorth'].rank(method='first', ascending=False) <= 20]
df_top20_sector['rank'] = df_top20_sector.groupby('industry_sector')['finalWorth'].rank(method='first', ascending=False)
df_top20_sector['rank'] = df_top20_sector['rank'].apply(lambda x: 'Top 5' if x <= 5.0 else 'Next 15')
df_top20_sector

/var/folders/6w/wjxnmjw11vb54wbgbg2cm_sw0000gn/T/ipykernel_29001/1888465617.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_top20_sector['rank'] = df_top20_sector.groupby('industry_sector')['finalWorth'].rank(method='first', ascending=False)
/var/folders/6w/wjxnmjw11vb54wbgbg2cm_sw0000gn/T/ipykernel_29001/1888465617.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_top20_sector['rank'] = df_top20_sector['rank'].apply(lambda x: 'Top 5' if x <= 5.0 else 'Next 15')


finalWorth                             personName   age   country  \
0         211000               Bernard Arnault & family  74.0    France   
1          80500  Francoise Bettencourt Meyers & family  69.0    France   
2          40100              François Pinault & family  86.0    France   
4           9800                     Jacques Saadé, Jr.  51.0    France   
5           9800                         Rodolphe Saadé  53.0    France   
...          ...                                    ...   ...       ...   
2115        9200        Antonia Ax:son Johnson & family  79.0    Sweden   
2139       14900                    Dhanin Chearavanont  83.0  Thailand   
2215        8200                       Abdulsamad Rabiu  62.0   Nigeria   
2216        8200                       Abdulsamad Rabiu  62.0   Nigeria   
2375       10100                         Quek Leng Chan  81.0  Malaysia   

            industries                status gender  birthDate  gdp_country  \
0     Fashion & Retail                     U      M 1949-03-05     0.000272   
1     Fashion & Retail                     U      F 1953-07-10     0.000272   
2     Fashion & Retail                     D      M 1936-08-21     0.000272   
4            Logistics  Split Family Fortune      M 1971-08-10     0.000272   
5            Logistics  Split Family Fortune      M 1970-03-03     0.000272   
...                ...                   ...    ...        ...          ...   
2115       Diversified                     U      F 1943-09-06     0.000053   
2139       Diversified                     U      M 1939-04-19     0.000054   
2215       Diversified                     U      M 1960-08-04     0.000045   
2216       Diversified                     U      M 1960-08-04     0.000045   
2375       Diversified                     D      M 1941-08-12     0.000036   

      life_expectancy_country  total_tax_rate_country  economic_class  \
0                        82.5                    60.7               1   
1                        82.5                    60.7               1   
2                        82.5                    60.7               1   
4                        82.5                    60.7               1   
5                        82.5                    60.7               1   
...                       ...                     ...             ...   
2115                     82.5                    49.1               1   
2139                     76.9                    29.5               2   
2215                     54.3                    34.8               2   
2216                     54.3                    34.8               3   
2375                     76.0                    38.7               2   

      education continent                   industry_sector    year  decade  \
0           3.0    Europe  Consumer Discretionary & Staples  1949.0  1940.0   
1           NaN    Europe  Consumer Discretionary & Staples  1953.0  1950.0   
2           0.0    Europe  Consumer Discretionary & Staples  1936.0  1930.0   
4           NaN    Europe                           Service  1971.0  1970.0   
5           NaN    Europe                           Service  1970.0  1970.0   
...         ...       ...                               ...     ...     ...   
2115        4.0    Europe                       Diversified  1943.0  1940.0   
2139        NaN      Asia                       Diversified  1939.0  1930.0   
2215        NaN    Africa                       Diversified  1960.0  1960.0   
2216        NaN    Africa                       Diversified  1960.0  1960.0   
2375        3.0      Asia                       Diversified  1941.0  1940.0   

         e_class  medianFinalWorth     rank  
0      Developed            4200.0    Top 5  
1      Developed            4200.0    Top 5  
2      Developed            4200.0  Next 15  
4      Developed            4200.0  Next 15  
5      Developed            4200.0  Next 15  
...          ...               ...      ...  
2115   D

In [27]:
alt.Chart(df_top20_sector).mark_bar().encode(
    alt.X('sum(finalWorth):Q', ).title('Final Net Worth (Million USD)'),
    alt.Y('rank:N').title(''),
    alt.Color('economic_class:O').title('Economic Class'),
    alt.Row('industry_sector:N', header=alt.Header(labelAngle=0, labelAlign='left')).title('Industry Sector'),
    alt.Tooltip(['sum(finalWorth)', 'economic_class', 'count()'])
).properties(
    title='Total Final Net Worth of Top 20 Billionaires by Industry Sector'
)

alt.Chart(...)

### Task 7

In [32]:
# Trying to add interaction that selects the attribute to be encoded on the Row channel... Not working... Need to ask TA

#task_7_row_attr = ['continent', 'industry_sector', 'education', 'economic_class']
#task_7_drop_down = alt.binding_select(options=task_7_row_attr, name='Attribute:')
#task_7_select = alt.selection_point(fields=['continent'], bind=task_7_drop_down)
#task_7_op_rowAttr = alt.param(value='continent', bind=task_7_drop_down)

In [28]:
task7_continent = alt.Chart(df.dropna()).mark_bar().encode(
    alt.X('min(finalWorth):Q', axis=alt.Axis(grid=False)).title('Final Net Worth Range (million USD)'),
    alt.X2('max(finalWorth):Q'),
    alt.Y('gender:N').title(''),
    alt.Color('gender:N').title('Gender'),
    alt.Row('continent:N').title('Continent')
).properties(
    width=150,
    height=30
)

In [29]:
task_7_industry_sector = task7_continent.encode(
    alt.Row('industry_sector:N', header=alt.Header(labelAngle=0, labelAlign='left')).title('Industry Sector')
)

In [30]:
task_7_education = task7_continent.encode(
    alt.Row('education:N').title('Education Level')
)

In [31]:
task_7_economic_class = task7_continent.encode(
    alt.Row('economic_class:N').title('Economic Class')
)

In [32]:
task_7_plot = (task7_continent | task_7_economic_class) & (task_7_education | task_7_industry_sector)
task_7_plot

alt.VConcatChart(...)